We will now define RS (regular spiking) excitatory neuron and FS (fast spiking) inhibitory neuron. These 2 types are enough to model part of the cortex in terms of dynamical system.

These parituclar parameters were taken from Izhikevich's book (2004).

In [1]:
import numpy as np
from scipy.integrate import ode #solving DE
import plotly.subplots as sp #visualizations
import plotly.graph_objs as go #visualizations

#LaTeX workaround
import plotly
from IPython.display import display, HTML
plotly.offline.init_notebook_mode()
display(HTML(
    '<script type="text/javascript" async src="https://cdnjs.cloudflare.com/ajax/libs/mathjax/2.7.1/MathJax.js?config=TeX-MML-AM_SVG"></script>'
))

## Consts

In [17]:
V_PEAK_PARAM = "v_peak"
A_PARAM = "a"
B_PARAM = "b"
c_PARAM = "c"
D_PARAM = "d"

C_PARAM = "C"
K_PARAM = "k"
V_R_PARAM = "v_r"
V_T_PARAM = "v_t"

# Utils

In [8]:
def plot_membrane_voltage(v: np.array, T: np.array):
    """Plots membrane potential progression over the time."""
    fig = go.Figure()

    trace = go.Scatter(x=T, y=v, mode='lines', name=r"$\text{Membrane voltage} \: (\text{in} \: mV)$")
    fig.add_trace(trace)

    fig.update_layout(title='Membrane voltage',
                      xaxis_title=r'$\text{Time} \: (\text{in} \: ms)$',
                      yaxis_title=r'$mV$')
    
    return trace, fig

In [9]:
def plot_membrane_voltage_against_recovery(voltage: np.array, recovery_variable: np.array):
    """Plots membrane voltage against recovery variable progression over the time forming dynamical plot.
    x-axis - recovery variable (u)
    y-axis - membrane voltage (v)"""
    fig = go.Figure()

    trace = go.Scatter(x=recovery_variable, y=voltage, mode='lines', name='Membrane voltage (in mV) against recovery variable (u)')

    fig.add_trace(go.Scatter(x=recovery_variable, y=voltage, mode='lines', name='Membrane voltage (in mV) against potassium recovery variable (u)'))

    fig.update_layout(title='Membrane voltage against recovery variable',
                      yaxis_title='mV')
    
    return trace, fig

# Excitatory RS Neuron

In [30]:
C_RS = 100 #membrane capacitance
a_RS = 0.03 #recovery time constant
b_RS = -2 #determines whether u is an amplifying (b < 0) or resonant (b > 0)
c_RS = -50 #voltage reset value
d_RS = 100 #total amount of outward minus inward currents activated during the spike and affecting the after-spike behavior

v_r_RS = - 60 #resting membrane potential
v_t_RS = - 40 #instantaneous threshold potential
v_peak_RS = 35 #spike cutoff value

k_RS = 0.7

v_RS = v_r_RS #membrane potential
u_RS = 0 #recovery current

start_state = np.array([v_RS, u_RS])

params_RS = {A_PARAM: a_RS, 
          B_PARAM: b_RS, 
          c_PARAM: c_RS, 
          D_PARAM: d_RS, 
          C_PARAM: C_RS, 
          K_PARAM: k_RS, 
          V_PEAK_PARAM: v_peak_RS, 
          V_R_PARAM: v_r_RS, 
          V_T_PARAM: v_t_RS}

In [37]:
t_min = 0
t_max = 1000
sim_steps = 10000

T = np.linspace(t_min, t_max, sim_steps)
delta_T = t_max/sim_steps

In [38]:
def simulation_run(res_state: np.ndarray, I, T: np.ndarray, delta_T: float, params: dict):
    v_curr, u_curr = res_state
    v = [v_curr]
    u = [u_curr]
    for i in range(len(T)):
        if v_curr >= params[V_PEAK_PARAM]:
            v_new = params[c_PARAM]
            u_new = u_curr + params[D_PARAM]
        else:
            v_new = v_curr + delta_T*(params[K_PARAM]*(v_curr - params[V_R_PARAM])*(v_curr - params[V_T_PARAM]) - u_curr + I(T[i]))/params[C_PARAM]
            u_new = u_curr + delta_T*params[A_PARAM]*(params[B_PARAM]*(v_curr - params[V_R_PARAM]) - u_curr)
        
        v_curr = v_new
        u_curr = u_new
        v.append(v_curr)
        u.append(u_curr)
    
    return v, u

## DC Current

In [49]:
def I_dc(t):
    if t > 100.0:
        return 70.0
    return 0.0

In [42]:
v, u = simulation_run(start_state, I_dc, T, delta_T, params_RS)

In [43]:
_, fig = plot_membrane_voltage(v, T)
fig.show()

In [44]:
_, fig = plot_membrane_voltage_against_recovery(v, u)
fig.show()

# Inhibitory FS Interneuron

In [50]:
C_FS = 20 #membrane capacitance
a_FS = 0.2 #recovery time constant
b_FS = 0.025
c_FS = -45 #voltage reset value
d_FS = 100 #total amount of outward minus inward currents activated during the spike and affecting the after-spike behavior

v_r_FS = - 55 #resting membrane potential
v_t_FS = - 40 #instantaneous threshold potential
v_peak_FS = 25 #spike cutoff value

k_FS = 1

v_FS = v_r_FS #membrane potential
u_FS = 0 #recovery current

start_state = np.array([v_FS, u_FS])

params_FS = {A_PARAM: a_FS, 
          B_PARAM: b_FS, 
          c_PARAM: c_FS, 
          D_PARAM: d_FS, 
          C_PARAM: C_FS, 
          K_PARAM: k_FS, 
          V_PEAK_PARAM: v_peak_FS, 
          V_R_PARAM: v_r_FS, 
          V_T_PARAM: v_t_FS}

Wow! Awesome threshold around 70(pA). Neuron fires at constant rate if I_DC value is greater then 73(pA).

In [99]:
def I_DC_FS(t):
    if t > 100.0:
        return 73.0
    return 0.0

In [100]:
def simulation_run_FS(res_state: np.ndarray, I, T: np.ndarray, delta_T: float, params: dict):
    v_curr, u_curr = res_state
    v = [v_curr]
    u = [u_curr]
    for i in range(len(T)):
        if v_curr >= params[V_PEAK_PARAM]:
            v_new = params[c_PARAM]
            u_new = u_curr
        else:
            if v_curr >= params[V_R_PARAM]:
                U_v_curr = params[B_PARAM]*(v_curr - params[V_R_PARAM])**3
            else:
                U_v_curr = 0
            v_new = v_curr + delta_T*(params[K_PARAM]*(v_curr - params[V_R_PARAM])*(v_curr - params[V_T_PARAM]) - u_curr + I(T[i]))/params[C_PARAM]
            u_new = u_curr + delta_T*params[A_PARAM]*(U_v_curr - u_curr)
        
        v_curr = v_new
        u_curr = u_new
        v.append(v_curr)
        u.append(u_curr)
    
    return v, u

In [101]:
v, u = simulation_run_FS(start_state, I_DC_FS, T, delta_T, params_FS)

In [102]:
_, fig = plot_membrane_voltage(v, T)
fig.show()

# Synapse Model